This notebook can be executed on either cpu or gpu runtime.

To run on gpu, change the
```
.to('cpu')
```
to

```
.to('gpu')
```

In [1]:
# Download nessecary libraries
!pip install datasets==2.10.0 --quiet
!pip install transformers --quiet

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 469.0/469.0 kB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 6.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 2.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 5.2 MB/s eta 0:00:00


In [2]:
from google.colab import drive
drive.mount('/content/drive/')
root_dir = "./drive/MyDrive/ASR_Colab/" #change it to your own path

Mounted at /content/drive/


In [3]:
# Load the preprocessed dataet
from datasets import load_from_disk
from os import path
import numpy as np

ds_test = load_from_disk(path.join(root_dir , "dataset.hf/test"))

In [4]:
ds_test

Dataset({
    features: ['voice_filename', 'transcript', 'accent', 'gender', 'tone', 'input_values', 'input_length', 'labels'],
    num_rows: 1153
})

In [4]:
from transformers import  Wav2Vec2CTCTokenizer ,Wav2Vec2FeatureExtractor,Wav2Vec2Processor

tokenizer = Wav2Vec2CTCTokenizer(path.join(root_dir ,"vocab.json"), unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [5]:
# Load the model weights
from transformers import Wav2Vec2ForCTC
model = Wav2Vec2ForCTC.from_pretrained(path.join(root_dir ,"model_weights")).to("cpu")
# model = Wav2Vec2ForCTC.from_pretrained(path.join(root_dir ,"model_weights")).to("cuda")

In [7]:
# select 20 random samples from the test dataset
selected_samples = np.random.randint(low = 0 , high= len(ds_test) , size=20)

In [8]:
import torch

# Initialize empty lists to store predicted outputs and other columns
predicted = []
real_sentences = []
audios = []
gender = []
accent = []
tone = []


# Iterate through the selected samples in the test dataset
for sample in ds_test.select(selected_samples):
  model_input = processor(sample["input_values"], return_tensors="pt", padding=True,sampling_rate=16000)

  # Move the input values to GPU and obtain model predictions
  logits = model(model_input.input_values.to("cpu")).logits
  pred_ids = torch.argmax(logits, dim=-1)[0]

  # Append the predicted output, real sentence labels, and audio inputs and other columns to their respective lists
  predicted.append(pred_ids)
  real_sentences.append(sample["transcript"])
  audios.append(sample["input_values"])
  gender.append(sample["gender"])
  accent.append(sample["accent"])
  tone.append(sample["tone"])

In [9]:
import IPython.display as ipd

dashed = "_-_-"*100

prediction_strings = []

for id_sample in range(len(predicted)):
  # Display the predicted text generated by the model
  print("Prediction:")
  pred_str = processor.decode(predicted[id_sample])
  prediction_strings.append(pred_str)
  print(pred_str)

  # Display the reference (real) text
  print("\nReference:")
  print(real_sentences[id_sample])

  # Display the audio
  print("\nAudio:")
  speech = audios[id_sample]

  # Display the audio using IPython Audio with autoplay enabled
  ipd.display(ipd.Audio(data=speech, rate=16000))

  print(f'gender: {gender[id_sample]}, accent: {accent[id_sample]}, tone: {tone[id_sample]}')
  print(dashed)

Prediction:
چه تلاش شگفتانگیزی بود

Reference:
چه تلاش شگفتانگیزی بود 

Audio:


gender: female, accent: فارسی , tone: exclamatory
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
آیا فساد شادی و خشبختی تا رقم ععشار قابل انداز گیری و امتیازدهی هستند

Reference:
آیا فساد شادی و خوش بختی تا رقم اعشار قابل اندازه گیری و امتیاز دهی هستند 

Audio:


gender: male, accent: فارسی, tone: question
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
برای پاسخ دادم به این سال باید نگاه بسیار پایهای داشته باشیم

Reference:
برای پاسخ دادن به این سوال باید نگاه بسیار پایه ای داشته باشیم  

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
زبان فارسی زبانی زیبا و شیرین است

Reference:
زبان فارسی  زبانی زیبا و شیرین است 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
زبان فارسی در افقانستان به تور رسمی دری از هزا سیس چحلوسه خوشیدی و دار تاجی کستآن تاجیکی از دوره شع روی خانده میشود

Reference:
زبان فارسی در افغانستان به طور رسمی دری از  خورشیدی و در تاجیکستان تاجیکی از دوره شوروی خوانده می شود 

Audio:


...

gender: male, accent: فارسی, tone: normal 
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
امیشه محربان خواهم ماند حتتا اگر کسی قدر مهربهنیم را نداند

Reference:
همیشه مهربان خواهم ماند حتی اگر کسی قدر مهربانیم را نداند 

Audio:


gender: female, accent: ترکی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
ماری یا داوری است که زندگیای کوتاه اس

Reference:
بیماری یاداوری است که زندگی کوتاه است 

Audio:


gender: male , accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
و برای مداوای چشم در دشت انواه گرزها و آمپولها را به خود تذرح کرده اما ندیجه ا چندان این نگرفته بود

Reference:
و برای مداوای چشم دردش انواع قرصها و آمپولها را بخود تزریق کرده بود اما نتیجه چندانی نگرفته بود 

Audio:


gender: male, accent: فارسی , tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
مکانی که کوانتمی شاخهی از فیزیک نذری است

Reference:
مکانیک کوانتومی شاخه ای از فیزیک نظری است 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-


# Predict all test data

In [ ]:
import torch

pred_strings = []
for sample in ds_test:
    model_input = processor(sample["input_values"], return_tensors="pt", padding=True,sampling_rate=16000)

    logits = model(model_input.input_values.to("cpu")).logits
    pred_ids = torch.argmax(logits, dim=-1)[0]
    pred_str = processor.decode(pred_ids)
    pred_strings.append(pred_str)

# Calculate WER

In [ ]:
!pip install evaluate --quiet
!pip install jiwer --quiet

In [ ]:
# Load wer(Word Error Rate) metric
import evaluate

wer_metric = evaluate.load("wer")

def calculate_wer(pred, ref):
    return wer_metric.compute(predictions=pred, references=ref)

# process features

In [ ]:
df_test = ds_test.to_pandas()
df_test['gender'] = df_test['gender'].replace({'male ': 'male', 'مرد': 'male', 'Female': 'female'})
df_test['accent'] = df_test['accent'].replace({'فارسی ': 'فارسی', 'farsi': 'فارسی'})
df_test['tone'] = df_test['tone'].replace({'normal ': 'normal', 'nomal': 'normal', 'Question': 'question', 'exclamative': 'exclamatory', 'exclamatory ': 'exclamatory', 'Normal': 'normal', 'imperative ': 'imperative', 'question ': 'question', 'incomplete ': 'incomplete'})

In [ ]:
unique_gender = df_test['gender'].unique()
unique_accent = df_test['accent'].unique()
unique_tone = df_test['tone'].unique()

# Correlation between WER and gender

In [26]:
df_test['gender'].value_counts()

male      917
female    236
Name: gender, dtype: int64

In [52]:
gender_mapping = {k:v for k, v in zip(unique_gender, range(len(unique_gender)))}
print(gender_mapping)

gender_wer_vals = []
for k in gender_mapping.keys():
    indices = list(df_test[df_test['gender']==k].index)

    references = list(df_test.iloc[indices]['transcript'])
    preds = [pred_strings[i] for i in indices]

    wer_val = calculate_wer(preds, references)
    gender_wer_vals.append(wer_val)

print(gender_wer_vals)

{'male': 0, 'female': 1}
[0.4469602005640865, 0.3942663378545006]


In [7]:
import pandas as pd
from scipy.stats import pointbiserialr


# Calculate correlation using pointbiserialr correlation coefficient
correlation_coefficient, p_value = pointbiserialr(list(gender_mapping.values()), gender_wer_vals)

# Interpret the results
print(f"pointbiserialr Correlation Coefficient: {correlation_coefficient}")
print(f"P-value: {p_value}")

# Determine the nature of correlation
if correlation_coefficient > 0:
    print("Positive correlation: Higher gender values associated with higher WER.")
elif correlation_coefficient < 0:
    print("Negative correlation: Higher gender values associated with lower WER.")
else:
    print("No clear correlation.")

pointbiserialr Correlation Coefficient: -1.0
P-value: 1.0
Negative correlation: Higher gender values associated with lower WER.


# Correlation between WER and accent

In [56]:
df_test['accent'].value_counts()

فارسی      1124
ترکی         17
شیرازی        5
خراسانی       4
یزدی          3
Name: accent, dtype: int64

In [57]:
accent_mapping = {k:v for k, v in zip(unique_accent, range(len(unique_accent)))}
print(accent_mapping)

accent_wer_vals = []
for k in accent_mapping.keys():
    indices = list(df_test[df_test['accent']==k].index)

    references = list(df_test.iloc[indices]['transcript'])
    preds = [pred_strings[i] for i in indices]

    wer_val = calculate_wer(preds, references)
    accent_wer_vals.append(wer_val)

print(accent_wer_vals)

{'فارسی': 0, 'شیرازی': 1, 'ترکی': 2, 'خراسانی': 3, 'یزدی': 4}
[0.434566008813949, 0.5714285714285714, 0.45689655172413796, 0.6, 0.6904761904761905]


In [60]:
import pandas as pd
from scipy.stats import pointbiserialr


# Calculate correlation using pointbiserialr correlation coefficient
correlation_coefficient, p_value = pointbiserialr(list(accent_mapping.values()), accent_wer_vals)

# Interpret the results
print(f"pointbiserialr Correlation Coefficient: {correlation_coefficient}")
print(f"P-value: {p_value}")

# Determine the nature of correlation
if correlation_coefficient > 0:
    print("Positive correlation: Higher accent values associated with higher WER.")
elif correlation_coefficient < 0:
    print("Negative correlation: Higher accent values associated with lower WER.")
else:
    print("No clear correlation.")

pointbiserialr Correlation Coefficient: 0.8084143481726485
P-value: 0.09772064179865986
Positive correlation: Higher accent values associated with higher WER.


# Correlation between WER and tone

In [61]:
df_test['tone'].value_counts()

normal         896
question       109
exclamatory     56
imperative      50
incomplete      42
Name: tone, dtype: int64

In [62]:
tone_mapping = {k:v for k, v in zip(unique_tone, range(len(unique_tone)))}
print(tone_mapping)

tone_wer_vals = []
for k in tone_mapping.keys():
    indices = list(df_test[df_test['tone']==k].index)

    references = list(df_test.iloc[indices]['transcript'])
    preds = [pred_strings[i] for i in indices]

    wer_val = calculate_wer(preds, references)
    tone_wer_vals.append(wer_val)

print(tone_wer_vals)

{'normal': 0, 'question': 1, 'exclamatory': 2, 'imperative': 3, 'incomplete': 4}
[0.45209719857607183, 0.3459682977257064, 0.4112903225806452, 0.379746835443038, 0.3787878787878788]


In [63]:
import pandas as pd
from scipy.stats import pointbiserialr


# Calculate correlation using pointbiserialr correlation coefficient
correlation_coefficient, p_value = pointbiserialr(list(tone_mapping.values()), tone_wer_vals)

# Interpret the results
print(f"pointbiserialr Correlation Coefficient: {correlation_coefficient}")
print(f"P-value: {p_value}")

# Determine the nature of correlation
if correlation_coefficient > 0:
    print("Positive correlation: Higher tone values associated with higher WER.")
elif correlation_coefficient < 0:
    print("Negative correlation: Higher tone values associated with lower WER.")
else:
    print("No clear correlation.")

pointbiserialr Correlation Coefficient: -0.44551942537280464
P-value: 0.45211512286990835
Negative correlation: Higher tone values associated with lower WER.
